In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import json
import numpy as np
from torch.utils.data import Dataset, DataLoader
import glob
import wandb
import os
import torch.optim as optimizers
import pandas as pd
from copy import deepcopy
from ml_collections import ConfigDict 
import tqdm
import torch.nn.functional as F
import torch
import torch.nn as nn
from collections import defaultdict
import yaml
from sklearn.metrics import roc_auc_score
import networkx as nx
import functools

import sys
sys.path.append("../../src")
import dfs_code 
from dfs_transformer import collate_downstream, DFSCodeSeq2SeqFC, Trainer, KarateClubDataset
torch.multiprocessing.set_sharing_strategy('file_system')


2022-02-03 19:41:10.497432: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: :/opt/cuda/extras/CUPTI/lib64/:/opt/intel/lib:/opt/intel/mkl/lib/intel64:/opt/intel:/opt/ibm/ILOG/CPLEX_Studio1210/cplex/bin/x86-64_linux:/opt/ibm/ILOG/CPLEX_Studio1210/cplex/python/3.7/x86-64_linux:/opt/intel/clck_latest/lib:/opt/intel/daal/lib:/opt/intel/intelpython3/lib:/opt/intel/ipp/lib:/opt/intel/itac_2019/lib:/opt/intel/itac_latest/lib:/opt/intel/mkl/lib:/opt/intel/mkl_/lib:/opt/intel/mpirt/lib:/opt/intel/tbb/lib:/opt/intel/clck/2019.0/lib:/opt/intel/compilers_and_libraries_2019/linux/lib:/opt/intel/compilers_and_libraries/linux/lib:/opt/intel/itac/2019.0.018/lib:/opt/intel/itac_2019/intel64/lib:/opt/intel/itac_latest/intel64/lib:/opt/intel/parallel_studio_xe_2019.0.045/clck_2019/lib:/opt/intel/parallel_studio_xe_2019.0.045/itac_2019/l

In [3]:
graph_file = "/mnt/ssd/datasets/graphs/reddit_threads/reddit_edges.json"
label_file = "/mnt/ssd/datasets/graphs/reddit_threads/reddit_target.csv"
#graph_file = "/mnt/ssd/datasets/graphs/twitch_egos/twitch_edges.json"
#label_file = "/mnt/ssd/datasets/graphs/twitch_egos/twitch_target.csv"
batch_size = 50
rep = 1
max_edges = 200
n_epochs = 10
n_samples = None#10000 #10000

In [4]:
dataset = KarateClubDataset(graph_file, label_file, max_n=n_samples, max_edges=max_edges)

203088it [00:41, 4945.53it/s]
203088it [03:30, 962.56it/s] 


In [5]:
len(dataset)

203088

In [6]:
n = len(dataset)
n_train = int(0.8*n)
n_valid = 0
n_test = n - n_train - n_valid

perm = np.random.permutation(len(dataset))
train_idx = torch.tensor(perm[:n_train], dtype=torch.long)
valid_idx = torch.tensor(perm[n_train:n_train+n_valid].tolist(), dtype=torch.long)
test_idx = torch.tensor(perm[n_train+n_valid:].tolist(), dtype=torch.long)

In [7]:
ce = nn.CrossEntropyLoss() 

In [8]:
def collate_fn(dlist, use_min=False, rep=rep):
    dfs_codes = defaultdict(list)
    node_batch = [] 
    edge_batch = []
    y_batch = []
    rnd_code_batch = []
    nystroem_batch = []
    
    for d in dlist:
        for r in range(rep):
            edge_features = d.edge_features.clone()
            if use_min:
                code = d.min_dfs_code.clone()
                index = d.min_dfs_index.clone()
            else:
                code, index = dfs_code.rnd_dfs_code_from_edgeindex(d.edge_index.numpy(), 
                                                                   d.node_labels.numpy().tolist(), 
                                                                   d.edge_labels.numpy().tolist())

                code = torch.tensor(np.asarray(code), dtype=torch.long)
                index = torch.tensor(np.asarray(index), dtype=torch.long)


            rnd_code_batch += [code]
            node_batch += [d.node_features.clone()]
            edge_batch += [edge_features]
            y_batch += [d.y.unsqueeze(0).clone()]
            nystroem_batch += [d.nystroem.clone()]

    y = torch.cat(y_batch).unsqueeze(1)
    nystroem = torch.cat(nystroem_batch)

    
    for inp, nfeats, efeats in zip(rnd_code_batch, node_batch, edge_batch):
        dfs_codes['dfs_from'] += [inp[:, 0]]
        dfs_codes['dfs_to'] += [inp[:, 1]]
        atm_from_feats = nfeats[inp[:, -3]]
        atm_to_feats = nfeats[inp[:, -1]]
        bnd_feats = efeats[inp[:, -2]]
        dfs_codes['atm_from'] += [atm_from_feats]
        dfs_codes['atm_to'] += [atm_to_feats]
        dfs_codes['bnd'] += [bnd_feats]

    dfs_codes = {key: nn.utils.rnn.pad_sequence(values, padding_value=-1000).clone()
                 for key, values in dfs_codes.items()}
    return dfs_codes, y, nystroem

In [9]:
def collate_train(dlist, use_min=False, rep=rep):
    dfs_codes, y, _ = collate_fn(dlist, use_min=use_min, rep=rep)
    return dfs_codes, y

def collate_pretrain(dlist, use_min=False, rep=rep):
    dfs_codes, _, nystroem = collate_fn(dlist, use_min=use_min, rep=rep)
    return dfs_codes, nystroem

In [10]:
class TransformerCLS(nn.Module):
    def __init__(self, encoder, fingerprint='cls'):
        super(TransformerCLS, self).__init__()
        self.encoder = encoder
        self.fingerprint = fingerprint
    
    def forward(self, dfs_code):
        features = self.encoder.encode(dfs_code, method=self.fingerprint)
        return features

class TransformerPlusHead(nn.Module):
    def __init__(self, encoder, n_classes, fingerprint='cls'):
        super(TransformerPlusHead, self).__init__()
        self.encoder = encoder
        #self.head = nn.Linear(encoder.get_n_encoding(fingerprint), n_classes)
        self.head = nn.Sequential(nn.Linear(encoder.get_n_encoding(fingerprint), 128),
                                  nn.ReLU(inplace=True),
                                  nn.Linear(128, 128),
                                  nn.ReLU(inplace=True),
                                  nn.Linear(128, n_classes))
        self.fingerprint = fingerprint
    
    def forward(self, dfs_code):
        #with torch.no_grad():
        features = self.encoder.encode(dfs_code, method=self.fingerprint)
        output = self.head(features)
        return output

In [11]:
with open("../../config/selfattn/model/bert.yaml") as file:
    m = ConfigDict(yaml.load(file, Loader=yaml.FullLoader))
    
m["n_atoms"] = int(dataset.maxdegree)+1
m["n_bonds"] = 2
m["n_edge_features"] = 2
m["nlayers"] = 6
m["emb_dim"] = 120
m["nhead"] = 10
m["max_edges"] = max_edges
m["max_nodes"] = max_edges
m["dim_feedforward"] = 4*m["emb_dim"]
m["batch_size"] = batch_size
m["rep"] = rep
m["max_edges"] = max_edges
m["n_samples"] = n_samples
m["encoder_class"] = "DFSCodeEncoder"
m["use_min"] = False
m["training"] = {}
m["graph_file"] = graph_file


In [12]:
collate_fn2 = functools.partial(collate_train, use_min=m["use_min"])
collate_fn3 = functools.partial(collate_pretrain, use_min=m["use_min"])
trainloader = DataLoader(dataset, sampler=torch.utils.data.SubsetRandomSampler(train_idx), 
                         batch_size=batch_size, collate_fn=collate_fn2, num_workers=5)
validloader = DataLoader(dataset, sampler=torch.utils.data.SubsetRandomSampler(valid_idx), 
                         batch_size=batch_size, collate_fn=collate_fn2, num_workers=5)
testloader = DataLoader(dataset, sampler=torch.utils.data.SubsetRandomSampler(test_idx), 
                        batch_size=batch_size, collate_fn=collate_fn2, num_workers=5)

pretrainloader = DataLoader(dataset, sampler=torch.utils.data.SubsetRandomSampler(train_idx), 
                         batch_size=batch_size, collate_fn=collate_fn3, num_workers=5)
prevalidloader = DataLoader(dataset, sampler=torch.utils.data.SubsetRandomSampler(valid_idx), 
                         batch_size=batch_size, collate_fn=collate_fn3, num_workers=5)
pretestloader = DataLoader(dataset, sampler=torch.utils.data.SubsetRandomSampler(test_idx), 
                        batch_size=batch_size, collate_fn=collate_fn3, num_workers=5)

In [13]:
d = next(iter(trainloader))

In [14]:
d[0]['atm_from'].shape

torch.Size([100, 50, 466])

In [15]:
m["n_node_features"] = d[0]['atm_from'].shape[2]

In [16]:
encoder = DFSCodeSeq2SeqFC(**m)
premodel = TransformerCLS(encoder)
model = TransformerPlusHead(encoder, 2)

In [17]:
def loss_pretrain(pred, y, l=nn.MSELoss()):
    return l(pred, y)

def loss(pred, y, ce=ce):
    return ce(pred, y.squeeze())

def auc(pred, y):
    return roc_auc_score(y.detach().cpu().numpy(), pred[:, 1].detach().cpu().numpy())
    

In [18]:
run = wandb.init(mode="online", project="karateclub-twitch", entity="dfstransformer", 
                 config=m.to_dict(), job_type="evaluation", name="transformer-pretrained")

ERROR:wandb.jupyter:Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: chrisxx (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.12.10 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
2022-02-03 19:45:34.847236: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: :/opt/cuda/extras/CUPTI/lib64/:/opt/intel/lib:/opt/intel/mkl/lib/intel64:/opt/intel:/opt/ibm/ILOG/CPLEX_Studio1210/cplex/bin/x86-64_linux:/opt/ibm/ILOG/CPLEX_Studio1210/cplex/python/3.7/x86-64_linux:/opt/intel/clck_latest/lib:/opt/intel/daal/lib:/opt/intel/intelpython3/lib:/opt/intel/ipp/lib:/opt/intel/itac_2019/lib:/opt/intel/itac_latest/lib:/opt/intel/mkl/lib:/opt/intel/mkl_/lib:/opt/intel/mpir

In [19]:
pretrainer = Trainer(premodel, pretrainloader, loss_pretrain, lr=5*1e-5, validloader=pretestloader, 
                  es_period=1*n_train//batch_size, lr_adjustment_period=10*n_train//batch_size//4, wandb_run=run,
                  clip_gradient_norm=0.5, n_epochs=n_epochs)

trainer = Trainer(model, trainloader, loss, metrics={'auc': auc}, lr=5*1e-5, validloader=testloader, 
                  es_period=1*n_train//batch_size, lr_adjustment_period=10*n_train//batch_size//4, wandb_run=run,
                  clip_gradient_norm=0.5, n_epochs=n_epochs)

In [20]:
pretrainer.fit()

Valid 1: loss 0.540104:   3%|████▌                                                                                                                                                | 25/813 [00:02<00:36, 21.56it/s]


Valid 1: loss 0.546510:   7%|█████████▋                                                                                                                                           | 53/813 [00:03<00:31, 24.38it/s]


Valid 1: loss 0.555236:  10%|███████████████▏                                                                                                                                     | 83/813 [00:04<00:30, 23.90it/s]


Valid 1: loss 0.554550:  14%|████████████████████                                                                                                                                | 110/813 [00:05<00:29, 24.19it/s]


Valid 1: loss 0.557773:  17%|█████████████████████████▍                                                                                                                          | 140/813 [00:06<00:30, 22.42it/s]


...

Valid 10: loss 0.050183:  89%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌                | 722/813 [00:30<00:03, 25.34it/s]


Valid 10: loss 0.050319:  92%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌           | 750/813 [00:31<00:02, 25.16it/s]


Valid 10: loss 0.050279:  96%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊      | 779/813 [00:32<00:01, 24.94it/s]


Valid 10: loss 0.050586: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎| 809/813 [00:33<00:00, 23.59it/s]


Epoch 10: loss 0.061855: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3250/3250 [06:52<00:00,  7.88it/s]


In [21]:
trainer.fit()

Valid 1: loss 0.494273 0.7646:   3%|████▎                                                                                                                                         | 25/813 [00:02<00:39, 19.77it/s]


Valid 1: loss 0.489805 0.9392:   7%|█████████▎                                                                                                                                    | 53/813 [00:03<00:31, 24.09it/s]


Valid 1: loss 0.485308 0.8140:  10%|██████████████▋                                                                                                                               | 84/813 [00:04<00:32, 22.73it/s]


Valid 1: loss 0.485882 0.7965:  14%|███████████████████▎                                                                                                                         | 111/813 [00:05<00:28, 24.90it/s]


Valid 1: loss 0.485670 0.8128:  17%|████████████████████████▍                                                                                                                    | 141/813 [00:07<00:28, 23.68it/s]


...

Valid 10: loss 0.486674 0.8921:  96%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏     | 779/813 [00:33<00:01, 24.12it/s]


Valid 10: loss 0.486076 0.7537: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎| 809/813 [00:34<00:00, 23.01it/s]


Epoch 10: loss 0.489837 0.8397: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌| 3241/3250 [06:59<01:07,  7.49s/it]

EarlyStopping counter: 1 out of 100


Epoch 10: loss 0.489913 0.8396: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3250/3250 [07:00<00:00,  7.73it/s]
